# Markov Chain Monte Carlo: Implementation Issues
In this notebook we'll dig into the details of implementing MCMC.  It's an art.

Recall that there are several choices we have to make.  In particular, the **proposal distribution** can be chosen in many different ways; we saw two in the previous notebook.  The **acceptance** probability may also be selected in a number of different ways.

Let's go ahead and import our usual packages.

In [2]:
import numpy as np 
import pandas as pd 
import plotly.express as px 

## Alterations
The proposal distribution provides our proposed states.  Thus the proposal distribution should have the following three properties:

* We may sample from it.
* Samples are drawn quickly.
* The **support** (the states on which the probability is positive) should ideally be identical to that of the target distribution.  Practically speaking, the support of the proposal can be included in the support of the target, as long as the mass of the target off of the support of the proposal is very small.

As we've seen, the proposal may be independent of the current state, or not.  We saw an example using the uniform distribution on $-10\leq x\leq 10$ as our proposal distribution; this was independent of the current state.  We also saw some small jump proposal distributions that add a jump to the current state $x$; this depended on the current state of the system.

Are there other typical forms for proposals?  [1 pp 8-12] discusses several.  The Gibbs sampler is of most interest to us.  It's worth knowing that much work has been done since the publication of [1], including the now widely-used No U-Turn Sampler (NUTS) [4].

Other than the proposal distribution, what can be changed?  Some easy parameters to change are the length of the chains to create and the number of them.  Let's take a look at those alterations.

In [3]:
# Here's a little function putting together everything,
# including burn-in, the random walk through
# the state space, and the data handling.
def MCMC(target, proposal, acceptance, sample_size, initial,number_of_chains=1,burn_in=100):
    chains=[]
    for i in range(number_of_chains):
        # Initialize
        x = initial
        # Burn-in
        for i in range(burn_in):
            y = proposal(x)
            alpha = acceptance(x,y)
            u = np.random.uniform()
            if u < alpha:
                x = y
        # storage for the sample
        sample = np.array([x])
        for i in range(sample_size):
            y = proposal(x)
            alpha = acceptance(x,y)
            # dice roll of 100 sided die
            # if u < alpha, accept the proposed y
            # if u >= alpha, stay on x
            u = np.random.uniform()
            if u < alpha:
                x = y
            sample = np.append(sample,x)
        # appends list to list of lists chains !!note numpy array does vector addition with overloaded + operator, not append
        chains = chains + [list(sample)]
    return(np.array(chains))

Let's see how this works in action.

In [4]:
# Target Density
def f(x):
    return(1/np.sqrt(2*np.pi)*np.exp(-(x**2)/2))
# Proposal Density
def g(x=0):
    return(np.random.uniform(low=-10.0,high=10.0))
# Acceptance discipline
def A(x,y):
    return( min([1,f(y)/f(x)]))
samples = MCMC(f,g,A,5000,0.0,number_of_chains=10)

In [5]:
# numpy.shape gives the number of rows and the number of columns
# (rows, columns)
# 10 chains (row), 5001 samples per chain (column)
samples.shape

(10, 5001)

Our data is structured as a *numpy* array.  Each row is a sample of length 5001.  Can we plot this?  Would what a meaningful plot even mean?

Let's plot the evolution of a sample parameter - the sample mean - in each chain as time evolves.  This requires a bit of data processing, fairly common in data analytics.

In [6]:
means = []
number_chains,sample_size = samples.shape
for i in range(number_chains):
    evolution = np.array([samples[i,0]])
    for j in range(1,sample_size):
        evolution = np.append(evolution,np.mean(samples[i,0:j]))
    means = means + [evolution]
means = np.array(means)
the_names = ['X'+str(i) for i in range(number_chains)]
means_df = pd.DataFrame(dict(zip(the_names,means)))
px.line(means_df,title="Means of chains as more steps are added")

We're converging towards 0...sort of.  It seems as though a more accurate statement would be to say that the chains converge towards zero, but then level out.  Does a different proposal distribution achieve a different result?

In [7]:
def g(x):
    return(x + np.random.normal(scale=2.0))
samples2 = MCMC(f,g,A,5000,0.0,number_of_chains=10)
means = []
number_chains,sample_size = samples2.shape
for i in range(number_chains):
    evolution = np.array([samples2[i,0]])
    for j in range(1,sample_size):
        evolution = np.append(evolution,np.mean(samples2[i,0:j]))
    means = means + [evolution]
means = np.array(means)
the_names = ['X'+str(i) for i in range(number_chains)]
means_df = pd.DataFrame(dict(zip(the_names,means)))
px.line(means_df,title="Means of chains as more steps are added")

Is the convergence "better" with one proposal than with the other?  What would "better" mean?

Here, "better" might be taken to be "the variance in the samples after the behavior has settled down".  As an experiment, let's ensemble the chains in each sample and compute the standard deviation.  For proposal 1,

In [8]:
np.std(samples.flatten())

1.0107465021247934e+00

And for proposal 2,

In [9]:
np.std(samples2.flatten())

0.9981392629444292

Notice that the standard deviation for the two proposals is basically the same.  So this does not distinguish them.  Instead, we're going to try to estimate **mixing times** for each process.

Roughly, the mixing time for an MCMC process is the number of steps required for the chain to produce a sample whose histogram is "close to" the target density.  That is, the mixing time is the number of steps required for the MCMC process to produce a reasonably representative sample of the target density.

Let's work on this.  The first thing we will need is some means of "smoothing off" the histogram to a curve.  We would like to use a smoothing procedure that does not make any *a priori* assumptions on the shape of the smoothed histogram.  In particular, we don't want to *a priori* assume the smoothed histogram is normal.  We can use a kernel density smoother.

*Note*: The **scikit-learn** Python package has a number of useful machine learning tools.  For models, the usual workflow is to build the model as an object first, and then fit it to data with the **fit** method.  For example,

In [10]:
from sklearn.neighbors import KernelDensity
model = KernelDensity()
model.fit(samples[0,:].reshape(-1,1))

KernelDensity()

Now that we can smooth off the histogram, let's create a score from it.  We want to compare the smoothed histogram to the target density, which we have stored in the function $f$.  So, create some evenly spaced $x$-values, plug them into both the target $f$ and the smoothed histogram we created, compute the difference in outputs at each $x$-values, square, and sum.

In [11]:
x_space = np.linspace(-4,4,1000)
normal_values = f(x_space)
model_values = np.exp(model.score_samples(x_space[:,None]))
the_score = np.sum((normal_values - model_values)**2)
print(the_score)

2.31411127702719


Let's write all of this up into a function, *score*.  Ideally, I'd like to feed a sample and a bandwidth to *score*, and get the numerical score out.

In [12]:
def score(a_sample,bandwidth):
    model = KernelDensity(bandwidth=bandwidth)
    model.fit(a_sample.reshape(-1,1))
    model_values = np.exp(model.score_samples(x_space[:,None]))
    return( np.sum((normal_values - model_values)**2) )
score(samples[0,:],0.5)

0.19481616274237604

All right, let's run this.  In the interest of keeping the runtime down, I computed the score by throwing in an additional 10 sample points each pass through the loop.  This still may require a few minutes to execute (intel i3 processor on ubuntu ---> about 7.3 minutes).

In [13]:
test_bandwidth = 0.5
scores = []
number_chains,sample_size = samples.shape
for i in range(number_chains):
    evolution = np.array([samples[i,0]])
    for j in range(10,sample_size,10):
        evolution = np.append(evolution,score(samples[i,0:j],test_bandwidth))
    scores = scores + [evolution]
scores = np.array(scores)
the_names = ['X'+str(i) for i in range(number_chains)]
scores_df = pd.DataFrame(dict(zip(the_names,scores)))

Let's create the plot.  I've limited the ranges on the axes so that it is easier to compare the plots for the two different proposals.

In [14]:
fig = px.line(scores_df,title="Distance from normal distribution as more steps are added")
fig.update_xaxes(range = [0,300])
fig.update_yaxes(range = [0,2])
fig.show()

In [15]:
test_bandwidth = 0.5
scores = []
number_chains,sample_size = samples2.shape
for i in range(number_chains):
    evolution = np.array([samples2[i,0]])
    for j in range(10,sample_size,10):
        evolution = np.append(evolution,score(samples2[i,0:j],test_bandwidth))
    scores = scores + [evolution]
scores = np.array(scores)
the_names = ['X'+str(i) for i in range(number_chains)]
scores2_df = pd.DataFrame(dict(zip(the_names,scores)))

In [16]:
fig = px.line(scores2_df,title="Distance from normal distribution as more steps are added")
fig.update_xaxes(range = [0,300])
fig.update_yaxes(range = [0,2])
fig.show()

Comparing the graphs, it seems as though the mixing time for the second proposal is significantly lower.  That is, we have a representative sample with fewer sample points.

So how would this play out in practice?  Fast mixing times are helpful whenever it is computationally expensive to draw samples from the proposal, or when we are producing code intended for repeated use in other settings.  The investigation we've carried out here is part of the exploration and development of the code that will eventually be implemented.  Mixing times are one issue that come up in practice.  However, it's worth noting that other implementation issues occur on the hardware side, including how well the software design takes advantage of processor architecture.  We haven't worried about that here, but it seems clear that generating different chains are independent processes and can be carried out by different processors.

## References
1. Gilks, Richardson, Spiegelhalter (eds).  *Markov Chain Monte Carlo in Practice: Interdisiciplinary Statistics*.  Chapman & Hall, 1996.  A collection of articles from the previous millenium on implementing and applying MCMC.
2. Shonkwiler, Ronald W., and Franklin Mendivil. *Explorations in Monte Carlo Methods*. Springer Science & Business Media, 2009.  An introduction to sampling methods and MCMC.  Can be used for self-study.  Contains some excellent presentations of the connections between physics problems and the MCMC methods they inspired.
3. Brooks, Gelman, Jackson, Meng (eds). *Handbook of Markov Chain Monte Carlo*. CRC Press, 2011.
4. Hoffman, Gelman.  *The No U-Turn Sampler: Adaptively setting path lengths in Hamiltonian Monte Carlo*.  Journal of Machine Learning Research, 15.1 (2014), 1593-1623 (originally published in the arXiv in 2011).  The NUTS sampler is used in the Stan programming language.
